## TX output impedance

In a series of Fediverse toots starting [here](https://astrodon.social/@quantensalat/111654942242850354), Alexander Knochel DK3HD measured the output impedance of his Xiegu X6100 at 1 W output.

As a measurement device, he used a spectrum analyzer, which made possible some rather ingenious measurement approach.

The measurement setup is a resistive divider of a 1000&nbsp;Ω resistor `R1` in series with a 47&nbsp;Ω `R2`. There is a signal generator of unknown source impedance `Rs` that drives that divider. Alexander adds his TX in parallel to `R2`, which doubles as a dummy load. The signal generator and the TX operate at nearby, but different frequencies: 14.05 MHz the TX, 14 MHz the signal generator.

The measurement itself is done via a spectrum analyzer with input impedance of 50&nbsp;Ω. That spectrum analyzer is used in series with a 10&nbsp;kΩ resistor, leading to a total spectrum analyzer input impedance `Ra` of 10,050&nbsp;Ω.

Three measurement runs were done. In each measurement run, the spectrum analyzer was used to measure `Ua` parallel to the signal generator and `Ub` parallel to the TX.

Actually, the raw data as made available by the spectrum analyzer is in power, in dBm, so, rather, `Pa` and `Pb` are measured, from which `Ua` and `Ub` can be determined.

* In [measurement 1](https://astrodon.social/@quantensalat/111654978724862031), the TX was present and switched to SSB, but no audio frequency input was present, so the TX did not generate a signal of its own. Results: `Pa=-45.6 dBm, Pb=-80.1 dBm`.
* In [measurement 2](https://astrodon.social/@quantensalat/111654990868516067), the TX was completely removed, so the spectrum analyzer just measured the signal generator's output before and after attenuation via the resistive divider `R1` / `R2`. Results: `Pa=-45.1 dBm, Pb=-71.6 dBm`.
* In [measurement 3](https://astrodon.social/@quantensalat/111655003856290660), the TX was reconnected and set to AM to produce a 1&nbsp;W signal. The analyzer was used to determine the signal at the signal generator's frequency, not the (nearby) TX frequency. Results: `Pa=-25.85 dBm, Pb=-59.7 dBm`.
* There apparaently was a [measurement 4](https://astrodon.social/@quantensalat/111657012393091052) with a TX signal of 4&nbsp;W, but I did not find the raw data of that one; probably, Alexander has not published it.

In his analysis of these measurements, Alexander determined the TX impendance for the spectrum analyzer's signal to be 32.5&nbsp;Ω from measurement 1 and 36.1&nbsp;Ω from measurement 3. Just using the same calculation for measurement 2 should yield infinite impedance, as the TX was disconnected, but actually did yield -881&nbsp;Ω. Measurement 4 produced 40.8&nbsp;Ω.

His simplified analysis neglected `Ra`, treating it as high enough to ignore, and also treated `Rs` as low. In my more pedantic analysis that follows (as Python code), I use measurement 2 to estimate `Rs` (it comes out to 1360&nbsp;Ω) and also take `Ra` into account. With that analysis, I get 29.6&nbsp;Ω from measurement 1 and 33.6&nbsp;Ω from measurement 3.

In [1]:
import math
import scipy.optimize

def analyze_the_measurements(
    r1, r2, ra,
    pa1, pb1,
    pa2, pb2,
    pa3, pb3,
    trace):

    LOG10_of_50 = math.log(50) / math.log(10)

    def voltage_from_dbm(p):
        # Voltage, in Volt, across a 50 Ω load, from power, in dBm.
        return 10 ** (0.5 * (p/10 - 3 + LOG10_of_50))

    def parallel(rx, ry):
        # Parallel of two impendances.
        if rx == math.inf:
            return ry
        elif ry == math.inf:
            return rx
        else:
            return rx * ry / (rx + ry)

    def source_voltage_of_signal_generator(rs, rtx, pa):
        # Given an estimate of rs and rtx and an pa value,
        # estimate the source voltage of the signal generator
        # (it would exhibit into an open load).
        voltage_at_analyzer = voltage_from_dbm(pa)
        voltage_at_measurement_point = voltage_at_analyzer / 50 * ra
        resistor_at_analyzer = parallel(ra, r1 + parallel(r2, rtx))
        signal_generator_load_current = voltage_at_measurement_point / resistor_at_analyzer
        return signal_generator_load_current * (rs + resistor_at_analyzer)

    def estimated_ua(usig, rs, rtx):
        combined_load_at_r2 = parallel(r2, rtx)
        combined_load_at_r1 = parallel(ra, combined_load_at_r2 + r1)
        u_at_r1 = usig / (combined_load_at_r1 + rs) * combined_load_at_r1
        return u_at_r1 / ra * 50

    def estimated_ub(usig, rs, rtx):
        # Given an estimate for usig, rs, and rtx,
        # calculate the signal the analyzer should see, in volts.
        combined_load_sa_and_tx = parallel(ra, parallel(r2, rtx))
        signal_across_rtx = usig / (combined_load_sa_and_tx + r1 + rs) * combined_load_sa_and_tx
        return signal_across_rtx / ra * 50

    def voltage_quotient_seen(pa, pb):
        return voltage_from_dbm(pa) / voltage_from_dbm(pb)

    # Use the data from measurement 2 to estimate rs:
    uquot_meas_2 = voltage_quotient_seen(pa2, pb2)
    def uqot_calculated(rs, rtx):
        usig = source_voltage_of_signal_generator(rs, rtx, pa2)
        return estimated_ua(usig, rs, rtx) / estimated_ub(usig, rs, rtx)

    rs_low = 0
    rs_high = 1e6
    
    uquot_low = uqot_calculated(rs_low, math.inf)
    uquot_high = uqot_calculated(rs_high, math.inf)

    assert uquot_high < uquot_meas_2 < uquot_low

    sol_m2 = scipy.optimize.root_scalar(
        f=lambda rs: uqot_calculated(rs, math.inf)-uquot_meas_2,
        bracket=(rs_low, rs_high),
        method="brentq"
    )
    assert(sol_m2.converged)
    rs = sol_m2.root
    
    if trace:
        # print(f"U_signal_generator, simple analysis: {usig:.3} V")
        print("Measurement 2:")
        print(f"Estimated signal generator source voltage: {source_voltage_of_signal_generator(rs, math.inf, pa2):.3} V")
        print(f"Voltage quotient seen: {uquot_meas_2:.5} = 1/{1/uquot_meas_2:.5}")
        print(f"Quotient high rs: {uquot_high:.5}, low rs: {uquot_low:.5}")
        print(f"rs determined: {rs:.5}, quot is {uqot_calculated(rs, math.inf):.5}")

    # Now, calculate rtx from measurement 1
    uquot_meas_1 = voltage_quotient_seen(pa1, pb1)
    sol_mes1 = scipy.optimize.root_scalar(
        f=lambda rtx: uqot_calculated(rs, rtx)-uquot_meas_1,
        bracket=(1e-2, 1e5),
        method="brentq"
    )
    assert(sol_mes1.converged)
    rtx_1 = sol_mes1.root
    if trace:
        print("\nMeasurement 1:")
        print(f"Impendance of the tx is: {rtx_1:.3} Ω")

    # And that from measurement 3
    uquot_meas_3 = voltage_quotient_seen(pa3, pb3)
    sol_mes3 = scipy.optimize.root_scalar(
        f=lambda rtx: uqot_calculated(rs, rtx)-uquot_meas_3,
        bracket=(1e-2, 1e5),
        method="brentq"
    )
    assert(sol_mes3.converged)
    rtx_3 = sol_mes3.root
    if trace:
        print("\nMeasurement 3:")
        print(f"Impendance of the tx is: {rtx_3:.3} Ω")
    return (rtx_1, rtx_3)


analyze_the_measurements(
    r1=1000, r2=47, ra=10050,
    pa1=-45.6, pb1=-80.1,
    pa2=-45.1, pb2=-71.6,
    pa3=-25.85, pb3=-59.7,
    trace=True)

Measurement 2:
Estimated signal generator source voltage: 0.608 V
Voltage quotient seen: 21.135 = 1/0.047315
Quotient high rs: 20.271, low rs: 22.376
rs determined: 1359.5, quot is 21.135

Measurement 1:
Impendance of the tx is: 29.6 Ω

Measurement 3:
Impendance of the tx is: 33.6 Ω


(29.597606793504738, 33.625650469031996)

## How to reproduce?

* Install [Python](https://www.python.org/)
* Start a [`venv`](https://docs.python.org/3/library/venv.html)
* Activate that `venv`
* Run `pip install jupyter notebook scipy`
* Download `TX_Impedance_DK3HD.ipynb`, e.g., from [https://dj3ei.famsik.de/2023-TX_Impedance/TX_Impedance_DK3HD.ipynb](https://dj3ei.famsik.de/2023-TX_Impedance/TX_Impedance_DK3HD.ipynb).
* Run `jupyter lab`
* Wait for your browser to open, navigate to `TX_Impedance_DK3HD.ipynb`, and open.

## License (MIT)

Copyright 2023 Dr. Andreas Krüger, DJ3EI.

Permission is hereby granted, free of charge, to any person obtaining a copy of this software and associated documentation files (the “Software”), to deal in the Software without restriction, including without limitation the rights to use, copy, modify, merge, publish, distribute, sublicense, and/or sell copies of the Software, and to permit persons to whom the Software is furnished to do so, subject to the following conditions:

The above copyright notice and this permission notice shall be included in all copies or substantial portions of the Software.

THE SOFTWARE IS PROVIDED “AS IS”, WITHOUT WARRANTY OF ANY KIND, EXPRESS OR IMPLIED, INCLUDING BUT NOT LIMITED TO THE WARRANTIES OF MERCHANTABILITY, FITNESS FOR A PARTICULAR PURPOSE AND NONINFRINGEMENT. IN NO EVENT SHALL THE AUTHORS OR COPYRIGHT HOLDERS BE LIABLE FOR ANY CLAIM, DAMAGES OR OTHER LIABILITY, WHETHER IN AN ACTION OF CONTRACT, TORT OR OTHERWISE, ARISING FROM, OUT OF OR IN CONNECTION WITH THE SOFTWARE OR THE USE OR OTHER DEALINGS IN THE SOFTWARE.
